# Blurred Ball Cover

# Import Modules and Packages

In [1]:
%matplotlib inline
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
import random
from collections import namedtuple
import numpy.linalg as npl
from sets import Set

/Library/Python/2.7/site-packages/ipykernel_launcher.py:8: DeprecationWarning: the sets module is deprecated
  


# Declare Data Structures

In [2]:
Ball = namedtuple("Ball", ["center", "radius"])
BlurredBall = namedtuple("BlurredBall", ["k", "MEB"])

# Methods to Generate and Read Data

In [41]:
def generate_normal_data(num_of_points, num_of_dimensions):
    mean = random.sample(np.array(range(100)), num_of_dimensions)
    scalar_variances = 10.0 * np.ones(num_of_dimensions)
    covariance = np.diag(scalar_variances)
    points = np.random.multivariate_normal(mean, covariance, num_of_points)
    return points

def generate_multivariate_data(num_of_points, num_of_dimensions):
    probabilities = [float(1.0 / num_of_dimensions)] * num_of_dimensions
    points = np.random.multinomial(20, probabilities, size = num_of_points)
    return points

def read_data(data_file):
    data = []
    with open(data_file) as data_reader:
        lines = data_reader.readlines()
        for line in lines:
            values = line.split()
            values = values[1:]
            row = [float(value) for value in values]
            data.append(row)
        data = np.array(data)
        print(data.shape)
        return data, data.shape[0], data.shape[1]


# Helper Functions for Computing Clarkson's (2/epsilon)-coreset and MEB 

In [42]:
def inside_ball_eps(blurred_ball, point, epsilon):
    #print "inside_ball"
    center, radius = blurred_ball.MEB
    distance = npl.norm(point - center)
    if distance <= (1 + epsilon) * radius:
        return True
    else:
        return False

In [43]:
def approx_meb_light(points, epsilon):
    coreset = []
    num_of_points = len(points)
    furthest_point = None
    center = points[0]
    radius = 0.0
    num_iterations = int(1.0 / (epsilon * epsilon))
    distances = {}
    prev_radius = -10000.0
    coreset = [points[0]]
    for i in range(1, num_iterations):
        for j in range(num_of_points):
            distances[j] = npl.norm(points[j] - center)
        furthest_point_index = max(distances, key = distances.get)
        furthest_point = points[furthest_point_index]
        furthest_distance = distances[furthest_point_index]

        center = center + (1.0 / i) * (furthest_point - center)   
        if abs(furthest_distance - prev_radius) < 0.01:
            break
        prev_radius = furthest_distance
            
    radius = npl.norm(furthest_point - center)
    meb = Ball(center, radius)
    return meb

In [44]:
def epsilon_coreset(points, epsilon):
    coreset = []
    num_of_points = len(points)
    furthest_point = None
    center = points[0]
    radius = 0.0

    num_iterations = int(2.0 / (epsilon))
    print("Total Iterations: " + repr(num_iterations))
    distances = {}
    coreset_indices = Set()

    prev_radius = -10000.0
    
    coreset = [points[0]]
    for i in range(1, num_iterations):
        #print("Iteration: ", i, " radius: ", prev_radius)
        # Find furthest point
        for j in range(num_of_points):
            distances[j] = npl.norm(points[j] - center)
        # Calculated furthest point    
        furthest_point_index = max(distances, key = distances.get)
        furthest_point = points[furthest_point_index]
        furthest_distance = distances[furthest_point_index]
        if furthest_point_index in coreset_indices:
            continue
        coreset_indices.add(furthest_point_index)
        coreset.append(furthest_point)
        coreset_meb = approx_meb_light(coreset, 0.01)
        center = coreset_meb.center
        print center, coreset_meb.radius
        
    return coreset

# Clarkson's 2/epsilon coreset and MEB Algorithm

In [45]:
def approx_meb(points, epsilon):
    coreset = epsilon_coreset(points, epsilon)
    meb = approx_meb_light(coreset, epsilon)
    return BlurredBall(coreset, meb)
    

# Blurred Ball Cover Algorithm's Helper Method

In [46]:
def update(blurred_balls, A, epsilon):
    print "update"
    K = []
    for blurred_ball in blurred_balls:
        K.extend(blurred_ball.k)


    outer_loop_flag = False    
    for point in A:
        if outer_loop_flag == True:
            break
        for blurred_ball in blurred_balls:
            if inside_ball_eps(blurred_ball, point, epsilon) == False:
                outer_loop_flag = True
                break
                
    if outer_loop_flag == False:
        #print("This point is covered")
        return blurred_balls
    #else:
        #print("This point is not covered")
        
    K_union_A = list(K)
    K_union_A.extend(A)
    blurred_ball_new = approx_meb(K_union_A, epsilon / 3.0)
    
    discardables = []
    for blurred_ball in blurred_balls:
        lhs = blurred_ball.MEB.radius
        rhs = epsilon * blurred_ball_new.MEB.radius / 4.0
        #print("lhs <> rhs: " + repr(lhs) + " <> " + repr(rhs))
        if blurred_ball.MEB.radius <= (epsilon * blurred_ball_new.MEB.radius / 4.0):
            print "Found a discardable"
            discardables.append(blurred_ball)
    
    blurred_balls = [bb for bb in blurred_balls if bb not in np.array(discardables)]
    
    blurred_balls.append(blurred_ball_new)
    
    return blurred_balls
        

# Blurred Ball Cover Algorithm

In [47]:
def agarwal(points, num_of_points, num_of_dimensions):
    epsilon = 0.1
    batch_size = 100
    blurred_balls = []
    initial_points = points[0:num_of_dimensions, :]
    blurred_ball_init = approx_meb(initial_points, epsilon / 3.0)
    blurred_balls = [blurred_ball_init]

    for i in range(num_of_dimensions, num_of_points, batch_size):
        print "Iteration: " + repr(i)
        sid = i
        fid = min(i + batch_size, num_of_points)
        A = points[sid : fid, :]
        blurred_balls = update(blurred_balls, A, epsilon)
        
    return blurred_balls
  

# Drawing Utility Methods : For Debug and Visualization Purpose

In [48]:
def draw_blurred_balls(blurred_balls):
    xmin = min(points[:, 0])
    xmax = max(points[:, 0])
    ymin = min(points[:, 1])
    ymax = max(points[:, 1])

    print(xmin, xmax, ymin, ymax)
    # ball <- \phi
    ball = None
    count = 0
    processed_points = []
    fig, ax = plt.subplots(1, 1) 
    #ax.set_xlim(xmin - 10, xmax + 10)
    #ax.set_ylim(ymin - 10, ymax + 10)
    ax.set_aspect('equal', 'datalim')
    ax.set_xlim(xmin - 10, xmax + 10)
    ax.set_ylim(ymin - 10, ymax + 10)


    X = points[:, 0]
    Y = points[:, 1]
    scatters = plt.scatter(X, Y)

    for blurred_ball in blurred_balls:
        #print blurred_ball
        center, radius = blurred_ball.MEB
        circle = plt.Circle(center, radius, color='r', alpha = 0.1)
        ax.add_artist(circle)
        ax.add_artist(scatters)
    plt.show()

In [49]:
def draw_points_and_meb(points, meb):
    xmin = min(points[:, 0])
    xmax = max(points[:, 0])
    ymin = min(points[:, 1])
    ymax = max(points[:, 1])
    print(xmin, xmax, ymin, ymax)
    processed_points = []
    fig, ax = plt.subplots(1, 1) 
    #ax.set_xlim(xmin - 10, xmax + 10)
    #ax.set_ylim(ymin - 10, ymax + 10)
    ax.set_aspect('equal', 'datalim')
    ax.set_xlim(xmin - 50, xmax + 50)
    ax.set_ylim(ymin - 50, ymax + 50)
    X = points[:, 0]
    Y = points[:, 1]
    scatters = plt.scatter(X, Y)
    center = meb.center
    radius = meb.radius
    circle = plt.Circle(center, radius, color='r', alpha = 0.1)
    ax.add_artist(circle)

# Read Data from File

In [50]:
points, num_of_points, num_of_dimensions = read_data("ColorHistogram.asc")
print num_of_points, num_of_dimensions

(68040, 32)
68040 32


# Run Blurred Ball Cover Algorithm

In [51]:
blurred_balls = agarwal(points, num_of_points, num_of_dimensions)
#draw_blurred_balls(blurred_balls)

Total Iterations: 60
[  1.65995500e-01   2.61465000e-01   1.72435000e-02   3.16046000e-01
   8.07400000e-03   3.69900000e-03   2.16675000e-02   1.57135500e-01
   7.81500000e-04   2.09000000e-04   0.00000000e+00   0.00000000e+00
   3.33500000e-03   1.46050000e-03   2.60500000e-04   0.00000000e+00
   4.32400000e-03   1.30800000e-03   5.73500000e-04   1.04000000e-04
   2.29600000e-03   3.66500000e-04   2.60500000e-04   2.60500000e-04
   6.27500000e-04   1.56500000e-04   1.04000000e-04   1.56000000e-04
   8.18350000e-03   2.02610000e-02   3.48950000e-03   2.08500000e-04] 0.461272372371
[  1.64901500e-01   2.61468000e-01   1.94920000e-02   4.98169000e-01
   2.91750000e-03   1.57500000e-04   7.30000000e-04   3.54200000e-03
   4.17000000e-04   2.09000000e-04   0.00000000e+00   0.00000000e+00
   3.12650000e-03   1.46050000e-03   2.60500000e-04   0.00000000e+00
   3.95950000e-03   1.30800000e-03   5.73500000e-04   1.04000000e-04
   8.37500000e-04   3.66500000e-04   2.60500000e-04   2.60500000e-

/Library/Python/2.7/site-packages/ipykernel_launcher.py:36: DeprecationWarning: elementwise == comparison failed; this will raise an error in the future.


[  1.09400000e-03   0.00000000e+00   0.00000000e+00   3.10260500e-01
   5.15700000e-03   3.54500000e-03   2.15120000e-02   1.55366000e-01
   3.65000000e-04   5.00000000e-07   0.00000000e+00   0.00000000e+00
   2.09000000e-04   5.21500000e-04   1.04000000e-04   0.00000000e+00
   5.39500000e-04   1.12035000e-02   4.82604000e-01   5.26050000e-03
   1.63100000e-03   2.00000000e-06   0.00000000e+00   0.00000000e+00
   4.68500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00] 0.594949072298
[  1.13350000e-03   3.93750000e-05   1.56375000e-04   1.55365000e-01
   3.21500000e-03   2.08912500e-03   1.09525000e-02   7.80745000e-02
   5.74500000e-04   7.87500000e-05   0.00000000e+00   1.56375000e-04
   8.08500000e-04   5.47500000e-04   1.17000000e-04   3.90000000e-05
   5.80878750e-02   3.01303875e-01   3.63987750e-01   4.72800000e-03
   1.34368750e-02   3.47850000e-03   2.74125000e-04   7.42875000e-04
   3.90625000e-04 

   2.08500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00] 0.594949072298
[  9.60142857e-04   3.71428571e-05   0.00000000e+00   1.77291714e-01
   3.02157143e-03   2.02621429e-03   1.22927857e-02   8.87807857e-02
   3.57928571e-04   3.57142857e-07   0.00000000e+00   0.00000000e+00
   3.46285714e-04   3.72500000e-04   1.11428571e-04   0.00000000e+00
   1.13292857e-03   8.46071429e-03   3.45239643e-01   3.75785714e-03
   1.99878571e-03   1.08646429e-02   3.24181429e-01   1.77082143e-02
   5.28071429e-04   1.86071429e-04   0.00000000e+00   0.00000000e+00
   3.42357143e-04   3.71428571e-05   0.00000000e+00   3.71428571e-05] 0.686688083602
[  1.25021053e-03   3.83684211e-04   2.73684211e-05   9.80046316e-02
   2.31447368e-03   1.61610526e-03   6.82136842e-03   4.90634211e-02
   6.37000000e-04   2.46894737e-04   0.00000000e+00   0.00000000e+00
   8.09315789e-04   1.23410526e-03   2.02789474e-04   5.47368421e-05
   1.69300000e-03   9.93721053e-03   3.14494895e-01   2.47873737e-01
  

Iteration: 932
update
Total Iterations: 60
[  1.09400000e-03   0.00000000e+00   0.00000000e+00   3.10260500e-01
   5.15700000e-03   3.54500000e-03   2.15120000e-02   1.55366000e-01
   3.65000000e-04   5.00000000e-07   0.00000000e+00   0.00000000e+00
   2.09000000e-04   5.21500000e-04   1.04000000e-04   0.00000000e+00
   5.39500000e-04   1.12035000e-02   4.82604000e-01   5.26050000e-03
   1.63100000e-03   2.00000000e-06   0.00000000e+00   0.00000000e+00
   4.68500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00] 0.594949072298
[  9.60142857e-04   3.71428571e-05   0.00000000e+00   1.77291714e-01
   3.02157143e-03   2.02621429e-03   1.22927857e-02   8.87807857e-02
   3.57928571e-04   3.57142857e-07   0.00000000e+00   0.00000000e+00
   3.46285714e-04   3.72500000e-04   1.11428571e-04   0.00000000e+00
   1.13292857e-03   8.46071429e-03   3.45239643e-01   3.75785714e-03
   1.99878571e-03   1.08646429e-02   3.24181

...

[  6.84210526e-07   2.59146947e-01   3.93052632e-03   1.38473684e-04
   2.63185526e-01   2.63157895e-07   0.00000000e+00   0.00000000e+00
   0.00000000e+00   0.00000000e+00   0.00000000e+00   0.00000000e+00
   6.57894737e-04   0.00000000e+00   2.73684211e-05   2.19210526e-04
   2.06250105e-01   3.57452632e-03   1.64473684e-04   2.62746842e-01
   4.40000000e-05   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.10526316e-07   2.10526316e-07   0.00000000e+00   0.00000000e+00
   4.21052632e-07   1.68421053e-06   5.73684211e-06   8.63157895e-06] 0.841117076617
[  4.44444444e-07   2.18834667e-01   3.61900000e-03   2.21435222e-01
   2.22245556e-01   2.22222222e-07   0.00000000e+00   6.01777778e-04
   0.00000000e+00   0.00000000e+00   0.00000000e+00   0.00000000e+00
   3.47222222e-04   0.00000000e+00   2.31111111e-05   1.85111111e-04
   1.08854222e-01   1.88655556e-03   1.38888889e-04   2.21893111e-01
   2.32222222e-05   0.00000000e+00   0.00000000e+00   5.11111111e-06
   1.11111111e-07 

Iteration: 67532
update
Total Iterations: 60
[  1.09400000e-03   0.00000000e+00   2.00000000e-06   3.10302000e-01
   5.15650000e-03   3.54150000e-03   2.15105000e-02   1.55364500e-01
   3.64500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   5.20000000e-05   4.16500000e-04
   3.64500000e-04   0.00000000e+00   3.12500000e-04   4.99219000e-01
   1.45850000e-03   0.00000000e+00   0.00000000e+00   0.00000000e+00
   4.68500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   5.00000000e-07   8.00000000e-06] 0.608358092922
[  6.25142857e-04   0.00000000e+00   1.71428571e-06   1.77327286e-01
   2.88690571e-01   2.02371429e-03   1.22917143e-02   8.87797143e-02
   2.08285714e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   1.19142857e-04   0.00000000e+00   4.45714286e-05   3.57000000e-04
   2.08285714e-04   0.00000000e+00   2.67857143e-04   4.27902000e-01
   8.33428571e-04   0.00000000e+00   0.000

[  4.54545455e-07   1.79046636e-01   2.96145455e-03   1.82926818e-01
   1.81837818e-01   1.54545455e-06   4.54545455e-07   4.92727273e-04
   8.18181818e-07   2.27272727e-06   3.63636364e-07   2.72727273e-07
   2.84545455e-04   9.63636364e-05   3.82727273e-05   1.51636364e-04
   8.90943636e-02   3.58081818e-03   8.78599091e-02   1.82505455e-01
   5.03636364e-05   3.63636364e-07   0.00000000e+00   4.18181818e-06
   9.09090909e-08   9.09090909e-08   0.00000000e+00   0.00000000e+00
   1.81818182e-07   7.27272727e-07   2.54545455e-06   8.91620000e-02] 0.878978407951
[  1.98333333e-05   1.64126083e-01   2.71466667e-03   1.67682917e-01
   1.66685250e-01   1.50000000e-06   4.16666667e-07   4.51666667e-04
   7.50000000e-07   2.08333333e-06   3.33333333e-07   2.50000000e-07
   2.60833333e-04   8.83333333e-05   3.50833333e-05   1.39000000e-04
   8.24858333e-02   3.28241667e-03   8.05382500e-02   1.67296667e-01
   7.98658333e-02   4.34333333e-04   0.00000000e+00   3.83333333e-06
   2.24991667e-03 

[  6.84210526e-07   2.59146947e-01   3.93052632e-03   1.38473684e-04
   2.63185526e-01   2.63157895e-07   0.00000000e+00   0.00000000e+00
   0.00000000e+00   0.00000000e+00   0.00000000e+00   0.00000000e+00
   6.57894737e-04   0.00000000e+00   2.73684211e-05   2.19210526e-04
   2.06250105e-01   3.57452632e-03   1.64473684e-04   2.62746842e-01
   4.40000000e-05   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.10526316e-07   2.10526316e-07   0.00000000e+00   0.00000000e+00
   4.21052632e-07   1.68421053e-06   5.73684211e-06   8.63157895e-06] 0.841117076617
[  4.44444444e-07   2.18834667e-01   3.61900000e-03   2.21435222e-01
   2.22245556e-01   2.22222222e-07   0.00000000e+00   6.01777778e-04
   0.00000000e+00   0.00000000e+00   0.00000000e+00   0.00000000e+00
   3.47222222e-04   0.00000000e+00   2.31111111e-05   1.85111111e-04
   1.08854222e-01   1.88655556e-03   1.38888889e-04   2.21893111e-01
   2.32222222e-05   0.00000000e+00   0.00000000e+00   5.11111111e-06
   1.11111111e-07 

Iteration: 68032
update
Total Iterations: 60
[  1.09400000e-03   0.00000000e+00   2.00000000e-06   3.10302000e-01
   5.15650000e-03   3.54150000e-03   2.15105000e-02   1.55364500e-01
   3.64500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   5.20000000e-05   4.16500000e-04
   3.64500000e-04   0.00000000e+00   3.12500000e-04   4.99219000e-01
   1.45850000e-03   0.00000000e+00   0.00000000e+00   0.00000000e+00
   4.68500000e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   2.08500000e-04   0.00000000e+00   5.00000000e-07   8.00000000e-06] 0.608358092922
[  6.25142857e-04   0.00000000e+00   1.71428571e-06   1.77327286e-01
   2.88690571e-01   2.02371429e-03   1.22917143e-02   8.87797143e-02
   2.08285714e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   1.19142857e-04   0.00000000e+00   4.45714286e-05   3.57000000e-04
   2.08285714e-04   0.00000000e+00   2.67857143e-04   4.27902000e-01
   8.33428571e-04   0.00000000e+00   0.000

# Inspect Blurred Ball Cover's Output

In [53]:
for i in range(len(blurred_balls)):
    print i, len(blurred_balls[i].k), blurred_balls[i].MEB.radius

0 4 0.587598710874
1 3 0.492446380648
2 6 0.673123376196
3 6 0.720211157526
4 6 0.720211157526
5 6 0.723020568385
6 6 0.723020568385
7 8 0.791096924501
8 8 0.791096924501
9 9 0.808835038509
10 9 0.811564626478
11 9 0.824247936093
12 9 0.824247936093
13 9 0.824247936093
14 9 0.824247936093
15 9 0.824247936093
16 10 0.827843495099
17 10 0.827843495099
18 10 0.827843495099
19 10 0.827843495099
20 10 0.827843495099
21 10 0.827843495099
22 10 0.827843495099
23 10 0.827843495099
24 10 0.827843495099
25 11 0.827843495099
26 11 0.827843495099
27 11 0.827843495099
28 11 0.827843495099
29 11 0.841862128616
30 11 0.841862128616
31 11 0.835719088986
32 11 0.835719088986
33 11 0.835719088986
34 12 0.843175559324
35 12 0.842532294939
36 12 0.842532294939
37 12 0.842532294939
38 12 0.842532294939
39 12 0.842532294939
40 12 0.843225292072
41 11 0.855178178079
42 11 0.855178178079
43 11 0.854933115178
44 11 0.854933115178
45 11 0.854933115178
46 11 0.854933115178
47 11 0.854933115178
48 11 0.8549331151

# Write the Blurred Balls into a File

In [60]:
N = len(blurred_balls)
D = num_of_dimensions - 1

with open("histogram_balls.txt", "w") as outFile:
    outFile.write(repr(N) + " " + repr(D) + "\n")
    for ball in blurred_balls:
        print ball.MEB.center, ball.MEB.radius
        line = ""
        for d in range(D):
            line += repr(ball.MEB.center[d]) + " "
        line += repr(ball.MEB.radius) + "\n"
        outFile.write(line)
        #print line

[  1.11706083e-01   1.74495500e-01   1.36306667e-02   4.14424083e-01
   2.85700000e-03   1.12100000e-03   6.08166667e-04   2.65700000e-03
   4.75725000e-03   1.49358333e-03   1.04250000e-04   2.60000000e-05
   4.63298333e-02   2.95341667e-03   5.38166667e-04   5.20000000e-05
   6.54816667e-03   4.47050000e-03   7.90833333e-03   7.98583333e-04
   1.02198333e-02   1.02614333e-01   2.25954167e-02   6.08516667e-03
   5.13200000e-03   2.03388333e-02   1.16308333e-03   3.90500000e-04
   6.51466667e-03   2.08510833e-02   3.73258333e-03   2.98633333e-03] 0.587598710874
[  2.27615000e-02   1.04846000e-01   3.38772500e-01   3.17775500e-01
   1.72400000e-02   7.91650000e-03   2.16670000e-02   1.55364500e-01
   1.25000000e-03   1.04500000e-04   0.00000000e+00   0.00000000e+00
   7.81500000e-04   7.29500000e-04   0.00000000e+00   0.00000000e+00
   3.68500000e-04   3.13500000e-04   0.00000000e+00   0.00000000e+00
   1.45950000e-03   1.50000000e-06   0.00000000e+00   0.00000000e+00
   6.25000000e-04 

   5.06663636e-03   5.49636364e-04   1.97018182e-03   8.45294545e-02] 0.864909886687
[  8.73481818e-02   2.92936364e-03   8.39772727e-02   9.64031818e-02
   8.45940909e-02   1.01427273e-03   5.88090909e-04   2.39690909e-03
   1.56372727e-03   8.53636364e-05   1.70545455e-04   2.76554545e-03
   1.41572727e-03   1.71272727e-04   6.75454545e-05   3.23363636e-04
   9.03332727e-02   9.05880000e-02   8.89926364e-02   9.30030909e-02
   8.30147273e-02   3.07827273e-03   8.30492727e-02   8.39954545e-03
   1.59100000e-03   9.47272727e-05   9.45454545e-06   1.89090909e-05
   5.06663636e-03   5.49636364e-04   1.97018182e-03   8.45294545e-02] 0.864909886687
[  8.73481818e-02   2.92936364e-03   8.39772727e-02   9.64031818e-02
   8.45940909e-02   1.01427273e-03   5.88090909e-04   2.39690909e-03
   1.56372727e-03   8.53636364e-05   1.70545455e-04   2.76554545e-03
   1.41572727e-03   1.71272727e-04   6.75454545e-05   3.23363636e-04
   9.03332727e-02   9.05880000e-02   8.89926364e-02   9.30030909e-02
  

   7.76000000e-04   6.02333333e-04   2.39644444e-03   1.03290667e-01] 0.865631940673
[  1.04883889e-01   2.62922222e-03   1.71666667e-03   1.18080778e-01
   1.03265333e-01   1.21633333e-03   7.76555556e-04   3.26522222e-03
   1.86477778e-03   8.12222222e-05   2.43222222e-04   4.21355556e-03
   1.63677778e-03   2.09222222e-04   8.25555556e-05   4.41555556e-04
   1.12775667e-01   1.10714778e-01   1.08751444e-01   1.10862778e-01
   1.02663556e-01   2.55444444e-04   5.32555556e-04   1.75933333e-03
   1.15888889e-04   0.00000000e+00   0.00000000e+00   0.00000000e+00
   7.76000000e-04   6.02333333e-04   2.39644444e-03   1.03290667e-01] 0.865631940673
[  1.04883889e-01   2.62922222e-03   1.71666667e-03   1.18080778e-01
   1.03265333e-01   1.21633333e-03   7.76555556e-04   3.26522222e-03
   1.86477778e-03   8.12222222e-05   2.43222222e-04   4.21355556e-03
   1.63677778e-03   2.09222222e-04   8.25555556e-05   4.41555556e-04
   1.12775667e-01   1.10714778e-01   1.08751444e-01   1.10862778e-01
  

[  9.44057000e-02   2.43910000e-03   1.87830000e-03   1.06553800e-01
   9.24803000e-02   1.01150000e-03   6.98900000e-04   2.95950000e-03
   4.81400000e-04   5.25000000e-05   2.18900000e-04   3.80270000e-03
   7.66700000e-04   1.71400000e-04   7.47000000e-05   5.12200000e-04
   1.00802000e-01   9.89989000e-02   9.82309000e-02   1.03005600e-01
   9.24052000e-02   3.55300000e-04   4.79300000e-04   2.64600000e-03
   1.95990000e-03   9.23958000e-02   1.93750000e-03   8.33300000e-04
   7.50400000e-04   8.33800000e-04   2.56300000e-03   9.33991000e-02] 0.87064991767
[  9.44057000e-02   2.43910000e-03   1.87830000e-03   1.06553800e-01
   9.24803000e-02   1.01150000e-03   6.98900000e-04   2.95950000e-03
   4.81400000e-04   5.25000000e-05   2.18900000e-04   3.80270000e-03
   7.66700000e-04   1.71400000e-04   7.47000000e-05   5.12200000e-04
   1.00802000e-01   9.89989000e-02   9.82309000e-02   1.03005600e-01
   9.24052000e-02   3.55300000e-04   4.79300000e-04   2.64600000e-03
   1.95990000e-03  

[  3.43909091e-04   2.38818182e-04   1.25309091e-03   9.02090000e-02
   9.10060909e-02   4.25454545e-05   7.66363636e-05   6.25727273e-04
   1.84545455e-05   1.24390909e-03   1.18409091e-03   8.84946364e-02
   8.66597273e-02   8.65299091e-02   3.79000000e-03   4.09254545e-03
   9.06290000e-02   9.00886364e-02   8.97076364e-02   9.19840000e-02
   8.75125455e-02   6.06818182e-04   3.79090909e-05   1.86563636e-03
   4.14127273e-03   8.40056364e-02   1.76145455e-03   7.86090909e-04
   6.88181818e-05   2.65272727e-04   3.79000000e-04   4.53818182e-04] 0.886270017981
[  3.43909091e-04   2.38818182e-04   1.25309091e-03   9.02090000e-02
   9.10060909e-02   4.25454545e-05   7.66363636e-05   6.25727273e-04
   1.84545455e-05   1.24390909e-03   1.18409091e-03   8.84946364e-02
   8.66597273e-02   8.65299091e-02   3.79000000e-03   4.09254545e-03
   9.06290000e-02   9.00886364e-02   8.97076364e-02   9.19840000e-02
   8.75125455e-02   6.06818182e-04   3.79090909e-05   1.86563636e-03
   4.14127273e-03 

   1.48888889e-05   8.88888889e-07   1.45555556e-05   1.08986222e-01] 0.904983816
[  2.63333333e-05   1.09417889e-01   1.81111111e-03   1.12894222e-01
   1.11124222e-01   4.82222222e-05   9.31111111e-05   1.03055556e-03
   1.00000000e-06   1.44955556e-03   1.26200000e-03   1.06238889e-01
   3.47777778e-04   1.40888889e-04   1.62555556e-04   3.24222222e-04
   1.09981111e-01   4.37655556e-03   1.07314889e-01   1.12150444e-01
   1.06487778e-01   5.79111111e-04   1.15555556e-05   7.66444444e-04
   2.99988889e-03   1.16666667e-05   0.00000000e+00   3.47777778e-05
   1.48888889e-05   8.88888889e-07   1.45555556e-05   1.08986222e-01] 0.904983816
[  2.63333333e-05   1.09417889e-01   1.81111111e-03   1.12894222e-01
   1.11124222e-01   4.82222222e-05   9.31111111e-05   1.03055556e-03
   1.00000000e-06   1.44955556e-03   1.26200000e-03   1.06238889e-01
   3.47777778e-04   1.40888889e-04   1.62555556e-04   3.24222222e-04
   1.09981111e-01   4.37655556e-03   1.07314889e-01   1.12150444e-01
   1.064

In [55]:
import numpy as np
from sklearn.decomposition import PCA

def get_pca_transformer(points_hd):
    pca = PCA(n_components=2)
    pca.fit(points_hd)
    return pca

def get_blurred_ball_2d(blurred_ball, pca):
    points_hd = blurred_ball.k
    center_hd = blurred_ball.MEB.center
    points_hd.append(center_hd)
    
    points_2d = pca.fit_transform(points_hd)
    num_of_points = len(points_2d)
    center_2d = points_2d[num_of_points - 1, :]
    radius = blurred_ball.MEB.radius
    points_2d = points_2d[:num_of_points - 2, :]
    blurred_ball_2d = BlurredBall(points_2d, Ball(center_2d, radius))
    return blurred_ball_2d

In [56]:
'''
pca = get_pca_transformer(points)
blurred_balls_2d = [get_blurred_ball_2d(blurred_ball, pca) for blurred_ball in blurred_balls]
print(blurred_balls_2d[0])
draw_blurred_balls(blurred_balls_2d)
'''

'\npca = get_pca_transformer(points)\nblurred_balls_2d = [get_blurred_ball_2d(blurred_ball, pca) for blurred_ball in blurred_balls]\nprint(blurred_balls_2d[0])\ndraw_blurred_balls(blurred_balls_2d)\n'

# Timothy Chan's Algorithm

In [57]:
Ball = namedtuple("Ball", ["center", "radius"])

def inside_ball(ball, point):
    center, radius = ball
    distance = npl.norm(point - center)
    if distance < radius:
        return True
    else:
        return False

def meb_ball_and_point(ball, p):
    c, r = ball
    pc_scalar = npl.norm(c - p)
    pc_vector = c - p
    radius_unit = pc_vector / pc_scalar
    p_mirror = radius_unit * r + c
    c_prime = (p + p_mirror) / 2.0
    r_prime = npl.norm(p_mirror - p) / 2.0
    meb = Ball(c_prime, r_prime)
    return meb

def create_initial_ball(point):
    return Ball(point, 0.0)

def chan(points):
    count = 0
    center = None
    radius = None
    ball = None
    for point in points:
        if ball == None:
            ball = create_initial_ball(point)
            continue
        if inside_ball(ball, point):
            continue
        else:
            count += 1
            ball = meb_ball_and_point(ball, point)
            center, radius = ball
    return Ball(center, radius)

In [1]:
import random
points = random.shuffle(points)
meb = chan(points)
print(meb)
    

NameError: name 'points' is not defined

# TODO

## Compute MEB from MEBs

# Extension of Chan's Algorithm?